In [4]:
import os
import sys

links = ['https://drive.google.com/drive/folders/138z7UB0n-xlwrPP0yh1RL5q1a-ijOGNN',
         'https://drive.google.com/drive/folders/13thmylEd1kh1Fy3W3QhEK_T97EqOEghs',
         'https://drive.google.com/drive/folders/1-BkjKwB6pQQr5I0g3bFx9qvQ3bewZWqI',
         'https://drive.google.com/drive/folders/1CPG_zgU5iqv4v6F-e7hNuDHoitcE5b3Q']

In [2]:
%cd NewVideos

e:\Project\Pose\NewVideos


In [5]:
import gdown

for url in links:
    gdown.download_folder(url, quiet=True, use_cookies=False)

In [8]:
%cd ..

e:\Project\Pose


In [9]:
import cv2
import os

input_folder = "NewVideos"
output_folder = "newpics"

os.makedirs(output_folder, exist_ok=True)


for class_name in os.listdir(input_folder):
    class_path = os.path.join(input_folder, class_name)
    if not os.path.isdir(class_path):
        continue 

    output_class_path = os.path.join(output_folder, class_name)
    os.makedirs(output_class_path, exist_ok=True)


    for video_name in os.listdir(class_path):
        video_path = os.path.join(class_path, video_name)
        if not video_name.endswith(('.mp4', '.avi', '.mov', '.mkv')): 
            continue

        cap = cv2.VideoCapture(video_path)
        if not cap.isOpened():
            print(f"Không thể mở video: {video_path}")
            continue
        video_base_name = os.path.splitext(video_name)[0]

        frame_count = 0
        while True:
            ret, frame = cap.read()
            if not ret:
                break

            frame_filename = f"{output_class_path}/{video_base_name}_frame_{frame_count:04d}.jpg"
            cv2.imwrite(frame_filename, frame)
            frame_count += 1

        cap.release()
        print(f"Đã xử lý video: {video_path}, lưu {frame_count} frames vào {output_class_path}")

print("Hoàn tất xử lý tất cả video!")

Đã xử lý video: NewVideos\False\20241210_172540.mp4, lưu 9167 frames vào newpics\False
Đã xử lý video: NewVideos\False\20241210_173847.mp4, lưu 9156 frames vào newpics\False
Đã xử lý video: NewVideos\False\video_20241209_181558.mp4, lưu 11287 frames vào newpics\False
Đã xử lý video: NewVideos\False\video_20241209_183021.mp4, lưu 7582 frames vào newpics\False
Đã xử lý video: NewVideos\False\video_20241209_184608.mp4, lưu 8497 frames vào newpics\False
Đã xử lý video: NewVideos\False\video_20241210_171248.mp4, lưu 9199 frames vào newpics\False
Đã xử lý video: NewVideos\False\video_20241210_173907.mp4, lưu 7592 frames vào newpics\False
Đã xử lý video: NewVideos\False\VIDEO_DOWNLOAD_1733747152664_1733940797995.mp4, lưu 10159 frames vào newpics\False
Đã xử lý video: NewVideos\False\VIDEO_DOWNLOAD_1733747152908_1733940783383.mp4, lưu 9084 frames vào newpics\False
Đã xử lý video: NewVideos\False\VIDEO_DOWNLOAD_1733747153229_1733940770998.mp4, lưu 11428 frames vào newpics\False
Đã xử lý video: 

In [22]:
import mediapipe as mp
from mediapipe.tasks import python
from mediapipe.tasks.python import vision

In [23]:
mp_pose = mp.solutions.pose
pose = mp_pose.Pose(static_image_mode=True)
mp_drawing = mp.solutions.drawing_utils

In [27]:
import json
def extract_keypoints(image_path, confidence_threshold=0.5):
    image = cv2.imread(image_path)
    # Convert the image to RGB format as Mediapipe requires it
    image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    result = pose.process(image_rgb)

    if result.pose_landmarks:
        keypoints = []
        for lm in result.pose_landmarks.landmark:
            if lm.visibility < confidence_threshold:
                keypoints.append([0, 0, 0])  # Set values to 0 if confidence is below the threshold
            else:
                keypoints.append([lm.x, lm.y, lm.visibility])  # Add the keypoint if confidence is sufficient
        return keypoints
    return None  # Return None if no pose landmarks are detected


In [28]:
def process_folder(input_dir, output_dir):
    """
    Process all images in a folder and save extracted keypoints as JSON files.

    Args:
        input_dir (str): Path to the folder containing images.
        output_dir (str): Path to the folder to save JSON files.
    """
    os.makedirs(output_dir, exist_ok=True)
    for file_name in os.listdir(input_dir):
        if file_name.endswith(('.jpg', '.png', '.jpeg')):
            image_path = os.path.join(input_dir, file_name)
            keypoints = extract_keypoints(image_path)
            if keypoints:
                json_path = os.path.join(output_dir, file_name.replace('.jpg', '.json'))
                with open(json_path, 'w') as f:
                    json.dump(keypoints, f)
            else:
                print(f"Skipping {file_name}, no keypoints detected.")
                os.remove(image_path)

In [29]:
import os
import cv2
base_dir = r"E:\Project\Pose\newpics"
output_dir = r"E:\Project\Pose\keypoints_dataset_new"
for label in ["False", "True"]:
    input_path = os.path.join(base_dir, label)
    output_path = os.path.join(output_dir, label)
    process_folder(input_path, output_path)

Skipping cropped_flipped_video_20241209_183021_frame_3651.jpg, no keypoints detected.
Skipping cropped_flipped_video_20241209_182442_frame_1849.jpg, no keypoints detected.


In [8]:
import os

print(len(os.listdir("keypoints_dataset_new/False")), len(os.listdir("keypoints_dataset_new/True")))

5253 112926


In [6]:
import os
import random

folder_path = "newpics/True"

all_files = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

image_extensions = {'.jpg', '.jpeg', '.png', '.bmp', '.tiff'}
images = [f for f in all_files if os.path.splitext(f)[1].lower() in image_extensions]

random.shuffle(images)

num_to_delete = len(images) // 2

for img in images[:num_to_delete]:
    img_path = os.path.join(folder_path, img)
    try:
        os.remove(img_path)
        print(f"Đã xóa: {img}")
    except Exception as e:
        print(f"Lỗi khi xóa {img}: {e}")

print(f"Đã xóa {num_to_delete} ảnh trong thư mục.")


Đã xóa: VIDEO_DOWNLOAD_1733827089588_1733940744705_frame_1276.jpg
Đã xóa: flipped_20241210_171228_frame_1369.jpg
Đã xóa: VIDEO_DOWNLOAD_1733747153043_1733940779161_frame_3884.jpg
Đã xóa: VIDEO_DOWNLOAD_1733827089588_1733940744705_frame_5465.jpg
Đã xóa: flipped_video_20241209_184002_frame_5252.jpg
Đã xóa: 20241210_173142_frame_7198.jpg
Đã xóa: VIDEO_DOWNLOAD_1733747153312_1733940758609_frame_8379.jpg
Đã xóa: 20241210_171228_frame_4969.jpg
Đã xóa: video_20241209_182442_frame_5183.jpg
Đã xóa: flipped_20241210_170405_frame_8814.jpg
Đã xóa: 20241210_170405_frame_1112.jpg
Đã xóa: video_20241209_181028_frame_2306.jpg
Đã xóa: video_20241210_170432_frame_5419.jpg
Đã xóa: VIDEO_DOWNLOAD_1733747153312_1733940758609_frame_2770.jpg
Đã xóa: flipped_20241210_170405_frame_2295.jpg
Đã xóa: VIDEO_DOWNLOAD_1733827089389_1733940754344_frame_3201.jpg
Đã xóa: flipped_video_20241209_184002_frame_6494.jpg
Đã xóa: flipped_20241210_171228_frame_0033.jpg
Đã xóa: video_20241209_184002_frame_4380.jpg
Đã xóa: flipp

In [4]:
import os
from PIL import Image

# Đường dẫn đến thư mục chứa ảnh
folder_path = "newpics/True"

# Lấy danh sách tất cả các tệp trong thư mục
all_files = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

# Chỉ lọc ra các tệp ảnh (theo đuôi tệp phổ biến)
image_extensions = {'.jpg', '.jpeg', '.png', '.bmp', '.tiff'}
images = [f for f in all_files if os.path.splitext(f)[1].lower() in image_extensions]

# Flip và lưu ảnh
for img in images:
    img_path = os.path.join(folder_path, img)
    try:
        # Mở ảnh
        with Image.open(img_path) as image:
            # Flip ảnh theo chiều ngang (horizontal flip)
            flipped_image = image.transpose(Image.FLIP_LEFT_RIGHT)
            
            # Tạo tên mới cho ảnh flip và lưu lại trong cùng thư mục
            flipped_image_path = os.path.join(folder_path, f"flipped_{img}")
            flipped_image.save(flipped_image_path)
            print(f"Đã lưu ảnh flip: {flipped_image_path}")
    except Exception as e:
        print(f"Lỗi khi xử lý {img}: {e}")

print(f"Đã flip và lưu tất cả ảnh trong thư mục.")


Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0000.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0002.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0003.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0005.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0007.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0008.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0009.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0010.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0014.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0015.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0017.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0018.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0019.jpg
Đã lưu ảnh flip: newpics/True\flipped_20241210_170405_frame_0022.jpg
Đã lưu ảnh flip: newpics/True\flip

KeyboardInterrupt: 

In [8]:
import os
import random
from PIL import Image

# Đường dẫn đến thư mục chứa ảnh
folder_path = "newpics/False"

# Lấy danh sách tất cả các tệp trong thư mục
all_files = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

# Chỉ lọc ra các tệp ảnh (theo đuôi tệp phổ biến)
image_extensions = {'.jpg', '.jpeg', '.png', '.bmp', '.tiff'}
images = [f for f in all_files if os.path.splitext(f)[1].lower() in image_extensions]

# Chọn ngẫu nhiên 1/3 số ảnh trong thư mục
num_images_to_use = len(images) // 3
selected_images = random.sample(images, num_images_to_use)

# Cắt và lưu ảnh
for img in selected_images:
    img_path = os.path.join(folder_path, img)
    try:
        # Mở ảnh
        with Image.open(img_path) as image:
            # Lấy kích thước ảnh
            width, height = image.size

            # Cắt đi một nửa chiều cao ảnh (cắt phần dưới)
            cropped_image = image.crop((0, 0, width, height // 3))

            # Lưu ảnh đã cắt lại trong cùng thư mục với tên mới
            cropped_image_path = os.path.join(folder_path, f"cropped_{img}")
            cropped_image.save(cropped_image_path)
            print(f"Đã lưu ảnh đã cắt: {cropped_image_path}")
    except Exception as e:
        print(f"Lỗi khi xử lý {img}: {e}")

print(f"Đã cắt và lưu 1/3 số ảnh trong thư mục.")


Đã lưu ảnh đã cắt: newpics/False\cropped_flipped_VIDEO_DOWNLOAD_1733827478983_1733940749065_frame_9063.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_flipped_VIDEO_DOWNLOAD_1733747153229_1733940770998_frame_2725.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_flipped_video_20241210_173907_frame_2733.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_video_20241209_183021_frame_4616.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_20241210_173847_frame_0318.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_video_20241209_181558_frame_4765.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_VIDEO_DOWNLOAD_1733747152664_1733940797995_frame_3783.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_flipped_video_20241209_181558_frame_10849.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_flipped_VIDEO_DOWNLOAD_1733747152908_1733940783383_frame_2694.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_VIDEO_DOWNLOAD_1733747153229_1733940770998_frame_0289.jpg
Đã lưu ảnh đã cắt: newpics/False\cropped_flipped_VIDEO_DOWNLOAD_1733827089485_17

KeyboardInterrupt: 

In [20]:
import os
import random
from PIL import Image

# Đường dẫn đến thư mục chứa ảnh
folder_path = "newpics/True"
# Lấy danh sách tất cả các tệp trong thư mục
all_files = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

# Chỉ lọc ra các tệp ảnh (theo đuôi tệp phổ biến)
image_extensions = {'.jpg', '.jpeg', '.png', '.bmp', '.tiff'}
images = [f for f in all_files if os.path.splitext(f)[1].lower() in image_extensions]

# Chọn ngẫu nhiên 1/3 số ảnh trong thư mục
num_images_to_use = len(images) // 3
selected_images = random.sample(images, num_images_to_use)

# Cắt và lưu ảnh
for img in selected_images:
    img_path = os.path.join(folder_path, img)
    try:
        # Mở ảnh
        with Image.open(img_path) as image:
            # Lấy kích thước ảnh
            width, height = image.size

            # Cắt đi một nửa chiều cao ảnh (cắt phần dưới)
            cropped_image = image.crop((0, 0, width, height // 1.55))

            # Lưu ảnh đã cắt lại trong cùng thư mục với tên mới
            cropped_image_path = os.path.join(folder_path, f"cropped_{img}")
            cropped_image.save(cropped_image_path)
            print(f"Đã lưu ảnh đã cắt: {cropped_image_path}")
    except Exception as e:
        print(f"Lỗi khi xử lý {img}: {e}")

print(f"Đã cắt và lưu 1/3 số ảnh trong thư mục.")


Đã lưu ảnh đã cắt: newpics/True\cropped_VIDEO_DOWNLOAD_1733747153043_1733940779161_frame_5547.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_20241210_172007_frame_4570.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_20241210_171228_frame_10107.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_video_20241209_181028_frame_6274.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_20241210_173142_frame_0659.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_VIDEO_DOWNLOAD_1733747153043_1733940779161_frame_0955.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_flipped_video_20241209_184002_frame_3001.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_video_20241209_182442_frame_6562.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_20241210_171228_frame_1222.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_flipped_20241210_173142_frame_7653.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_video_20241209_181028_frame_5456.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_20241210_173142_frame_4153.jpg
Đã lưu ảnh đã cắt: newpics/True\cropped_VIDEO_DOWNLOA

In [18]:
import os

folder_path = "newpics/False"

# Lặp qua tất cả các file trong thư mục
for filename in os.listdir(folder_path):
    # Kiểm tra nếu "cropped" có trong tên file
    if "cropped" in filename:
        # Đường dẫn đầy đủ tới file
        file_path = os.path.join(folder_path, filename)
        # Xóa file
        os.remove(file_path)
        print(f"Đã xóa file: {file_path}")

print("Hoàn thành xóa các file chứa 'cropped' trong tên.")


Đã xóa file: newpics/False\cropped_20241210_172540_frame_0152.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_0217.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_0328.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_1244.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_2161.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_2942.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_3762.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_4061.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_5839.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_5894.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_6121.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_6792.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_7419.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_8413.jpg
Đã xóa file: newpics/False\cropped_20241210_172540_frame_8861.jpg
Đã xóa fil